In [1]:
import pandas as pd
import numpy as np
import sys

In [3]:
def sparse_training_data(file_path):
    samples = []
    with open(file_path, 'r') as file:
        for line in file:
            sample = line.strip().split(' ')
            m_labels = [int(label) for label in sample[0][2:].split(',')]
            s_labels = [int(label) for label in sample[1][2:].split(',')]
            features = ' '.join(sample[2:])
            samples.append((m_labels, s_labels, features))
    return samples


train_data = parse_training_data("IE506_2024_progchallenge_train.txt")

In [ ]:
# #2nd method for opening the file without using function\\
# with open(file_path, '"IE506_2024_progchallenge_train.txt"') as file:
#         for line in file:
#             sample = line.strip().split(' ')
#             m_labels = [int(label) for label in sample[0][2:].split(',')]
#             s_labels = [int(label) for label in sample[1][2:].split(',')]
#             features = ' '.join(sample[2:])
#             samples.append((m_labels, s_labels, features))
#     return samples

In [4]:
from scipy.sparse import dok_matrix

array_shape = (200000, 47236)
# array = np.zeros(array_shape, dtype=np.float32)
array = dok_matrix(array_shape, dtype=np.float32)


print(len(train_data))
# Iterate through each tuple
for i in range(len(train_data)):
    item = train_data[i]
    # Get the third element (which is a string)
    line = item[2]
    # Split the line into tokens
    tokens = line.split()
    # print(len(tokens), tokens)
    # Iterate through each token
    for token in tokens:
        feature_id, value = token.split(':')

        feature_id = int(feature_id)
        value = float(value)
        # print(feature_id, value)

        array[i, feature_id] = value
        
  

200000


In [6]:
array[100]

<1x47236 sparse matrix of type '<class 'numpy.float32'>'
	with 135 stored elements in Dictionary Of Keys format>

In [11]:
array.shape

(200000, 47236)

In [7]:
# Extracting unique main classes and subclasses
unique_main_classes = set()
unique_subclasses = set()
for main_class, subclass, _ in train_data:
    unique_main_classes.update(main_class)
    unique_subclasses.update(subclass)

# Create mapping from main class and subclass to column indices
main_class_mapping = {mc: idx for idx, mc in enumerate(sorted(unique_main_classes))}
subclass_mapping = {sc: idx for idx, sc in enumerate(sorted(unique_subclasses))}

# Create the matrix
num_rows = 200000
num_cols = len(unique_main_classes) + len(unique_subclasses)
matrix = [[0] * num_cols for _ in range(num_rows)]

# Fill in the matrix for Main class
for idx, (main_class, _, _) in enumerate(train_data):
    for mc in main_class:
        col_idx = main_class_mapping[mc]
        matrix[idx][col_idx] = 1

# Fill in the matrix for Subclass
for idx, (_, subclass, _) in enumerate(train_data):
    for sc in subclass:
        col_idx = len(unique_main_classes) + subclass_mapping[sc]
        matrix[idx][col_idx] = 1

# Print the matrix
for row in matrix[:10]:  # Print first 10 rows for example
    print(row)


[0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0]
[1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[1, 1, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0]
[1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1]
[0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1]
[1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 1, 0

In [8]:
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score

# Assuming X is your feature matrix and y is the target matrix
# X, y = load_your_data()

# Splitting the data into train and test sets
X_train, X_test, y_train, y_test = train_test_split(array, matrix, test_size=0.2, random_state=42)

# Initialize a list to store the trained logistic regression models
logistic_models = []

# Train a logistic regression model for each column of y
for i in range(y_train.shape[1]):
    # Create a logistic regression model
    clf = LogisticRegression()
    # Fit the model to the training data for the i-th column of y
    clf.fit(X_train, y_train[:, i])
    # Append the trained model to the list
    logistic_models.append(clf)

# Predicting on the test set
y_pred = []
for clf in logistic_models:
    y_pred.append(clf.predict(X_test))

# Convert the list of predictions into a 2D numpy array
y_pred = np.array(y_pred).T

# Calculate accuracy for each column and print
for i in range(y_test.shape[1]):
    accuracy = accuracy_score(y_test[:, i], y_pred[:, i])
    print(f"Accuracy for column {i+1}: {accuracy}")


AttributeError: 'list' object has no attribute 'shape'

In [ ]:
import numpy as np
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score

# Assuming X is your feature matrix and y is the target matrix
# X, y = load_your_data()

# Convert y_train and y_test into NumPy arrays
y_train = np.array(y_train)
y_test = np.array(y_test)

# Splitting the data into train and test sets
X_train, X_test, y_train, y_test = train_test_split(array, matrix, test_size=0.2, random_state=42)

# Initialize a list to store the trained logistic regression models
logistic_models = []

# Train a logistic regression model for each column of y
for i in range(y_train.shape[1]):
    # Create a logistic regression model
    clf = LogisticRegression()
    # Fit the model to the training data for the i-th column of y
    clf.fit(X_train, y_train[:, i])
    # Append the trained model to the list
    logistic_models.append(clf)

# Predicting on the test set
y_pred = []
for clf in logistic_models:
    y_pred.append(clf.predict(X_test))

# Convert the list of predictions into a 2D numpy array
y_pred = np.array(y_pred).T

# Calculate accuracy for each column and print
for i in range(y_test.shape[1]):
    accuracy = accuracy_score(y_test[:, i], y_pred[:, i])
    print(f"Accuracy for column {i+1}: {accuracy}")


In [7]:
matrix = np.array(matrix)

In [10]:
matrix.shape

(200000, 41)

## L2

In [11]:
import numpy as np
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score

# Assuming X is your feature matrix and y is the target matrix
# X, y = load_your_data()

# Convert y_train and y_test into NumPy arrays


# Splitting the data into train and test sets
X_train, X_test, y_train, y_test = train_test_split(array, matrix, test_size=0.2, random_state=42)
y_train = np.array(y_train)
y_test = np.array(y_test)

# Regularization strength
C = 0.1  # You can adjust this value

# Regularization type ('l1' or 'l2')
penalty = 'l2'  # You can change this to 'l1' if you want L1 regularization

# Train a logistic regression model for each column of y
logistic_models = []
for i in range(y_train.shape[1]):
    # Create a logistic regression model with regularization
    clf = LogisticRegression(penalty=penalty, C=C)
    # Fit the model to the training data for the i-th column of y
    clf.fit(X_train, y_train[:, i])
    # Append the trained model to the list
    logistic_models.append(clf)

# Predicting on the test set
y_pred = []
for clf in logistic_models:
    y_pred.append(clf.predict(X_test))

# Convert the list of predictions into a 2D numpy array
y_pred = np.array(y_pred).T

# Calculate accuracy for each column and print
for i in range(y_test.shape[1]):
    accuracy = accuracy_score(y_test[:, i], y_pred[:, i])
    print(f"Accuracy for column {i+1}: {accuracy}")

Accuracy for column 1: 0.93625
Accuracy for column 2: 0.937425
Accuracy for column 3: 0.955625
Accuracy for column 4: 0.958625
Accuracy for column 5: 0.9694
Accuracy for column 6: 0.987125
Accuracy for column 7: 0.95565
Accuracy for column 8: 0.991
Accuracy for column 9: 0.962
Accuracy for column 10: 0.997725
Accuracy for column 11: 0.968775
Accuracy for column 12: 0.9638
Accuracy for column 13: 0.969
Accuracy for column 14: 0.9907
Accuracy for column 15: 0.9969
Accuracy for column 16: 0.967825
Accuracy for column 17: 0.954275
Accuracy for column 18: 0.997625
Accuracy for column 19: 0.98145
Accuracy for column 20: 0.994825
Accuracy for column 21: 0.990075
Accuracy for column 22: 0.988525
Accuracy for column 23: 0.99645
Accuracy for column 24: 0.99015
Accuracy for column 25: 0.9737
Accuracy for column 26: 0.993575
Accuracy for column 27: 0.996925
Accuracy for column 28: 0.976575
Accuracy for column 29: 0.99715
Accuracy for column 30: 0.9848
Accuracy for column 31: 0.975425
Accuracy for 

## L1

In [14]:
import numpy as np
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score

# Assuming X is your feature matrix and y is the target matrix
# X, y = load_your_data()

# Convert y_train and y_test into NumPy arrays


# Splitting the data into train and test sets
X_train, X_test, y_train, y_test = train_test_split(array, matrix, test_size=0.2, random_state=42)
y_train = np.array(y_train)
y_test = np.array(y_test)

# Regularization strength
C = 0.1  # You can adjust this value

# Regularization type ('l1' or 'l2')
penalty = 'l1'  # You can change this to 'l1' if you want L1 regularization

# Train a logistic regression model for each column of y
logistic_models = []
for i in range(y_train.shape[1]):
    # Create a logistic regression model with regularization
    clf = LogisticRegression(penalty=penalty, C=C,solver='liblinear')
    # Fit the model to the training data for the i-th column of y
    clf.fit(X_train, y_train[:, i])
    # Append the trained model to the list
    logistic_models.append(clf)

# Predicting on the test set
y_pred = []
for clf in logistic_models:
    y_pred.append(clf.predict(X_test))

# Convert the list of predictions into a 2D numpy array
y_pred = np.array(y_pred).T

# Calculate accuracy for each column and print
for i in range(y_test.shape[1]):
    accuracy = accuracy_score(y_test[:, i], y_pred[:, i])
    print(f"Accuracy for column {i+1}: {accuracy}")

Accuracy for column 1: 0.926725
Accuracy for column 2: 0.93745
Accuracy for column 3: 0.954875
Accuracy for column 4: 0.95265
Accuracy for column 5: 0.9705
Accuracy for column 6: 0.98905
Accuracy for column 7: 0.957975
Accuracy for column 8: 0.99205
Accuracy for column 9: 0.96115
Accuracy for column 10: 0.99795
Accuracy for column 11: 0.970075
Accuracy for column 12: 0.9691
Accuracy for column 13: 0.9714
Accuracy for column 14: 0.99115
Accuracy for column 15: 0.996975
Accuracy for column 16: 0.968725
Accuracy for column 17: 0.955825
Accuracy for column 18: 0.997675
Accuracy for column 19: 0.983825
Accuracy for column 20: 0.995125
Accuracy for column 21: 0.9931
Accuracy for column 22: 0.990825
Accuracy for column 23: 0.99645
Accuracy for column 24: 0.99105
Accuracy for column 25: 0.9742
Accuracy for column 26: 0.995125
Accuracy for column 27: 0.997175
Accuracy for column 28: 0.97795
Accuracy for column 29: 0.9978
Accuracy for column 30: 0.988325
Accuracy for column 31: 0.97885
Accuracy 

In [19]:
y_pred.shape, y_test_binary.shape, y_test.shape

((40000, 41), (40000, 41), (40000, 41))

In [26]:
np.sum(np.sum((y_pred == y_test), axis=0)/40000)/41, np.sum(np.sum((y_pred == y_test), axis=1)/41)/40000

(0.980271951219512, 0.9802719512195123)

## L2 on full dataset

In [ ]:
import numpy as np
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score

# Assuming X is your feature matrix and y is the target matrix
# X, y = load_your_data()

# Convert y_train and y_test into NumPy arrays


# Splitting the data into train and test sets
# X_train, X_test, y_train, y_test = train_test_split(array, matrix, test_size=0.2, random_state=42)
# y_train = np.array(y_train)
# y_test = np.array(y_test)
matrix = np.array(matrix)

# Regularization strength
C = 0.1  # You can adjust this value

# Regularization type ('l1' or 'l2')
penalty = 'l2'  # You can change this to 'l1' if you want L1 regularization

# Train a logistic regression model for each column of y
L2_logistic_models = []
for i in range(matrix.shape[1]):
    # Create a logistic regression model with regularization
    clf = LogisticRegression(penalty=penalty, C=C)
    # Fit the model to the training data for the i-th column of y
    clf.fit(array, matrix[:, i])
    # Append the trained model to the list
    L2_logistic_models.append(clf)



# Predicting on the test set
y_pred = []
for clf in L2_logistic_models:
    y_pred.append(clf.predict(X_test))

# Convert the list of predictions into a 2D numpy array
y_pred = np.array(y_pred).T

# Calculate accuracy for each column and print
for i in range(y_test.shape[1]):
    accuracy = accuracy_score(y_test[:, i], y_pred[:, i])
    print(f"Accuracy for column {i+1}: {accuracy}")


print(np.sum(np.sum((y_pred == y_test), axis=0)/40000)/41, np.sum(np.sum((y_pred == y_test), axis=1)/41)/40000)

## L1 on full dataset

In [ ]:
import numpy as np
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
L1 on full dataset
import numpy as np
# Assuming X is your feature matrix and y is the target matrix
# X, y = load_your_data()

# Convert y_train and y_test into NumPy arrays


# Splitting the data into train and test sets
# X_train, X_test, y_train, y_test = train_test_split(array, matrix, test_size=0.2, random_state=42)
# y_train = np.array(y_train)
# y_test = np.array(y_test)
matrix = np.array(matrix)

# Regularization strength
C = 0.1  # You can adjust this value

# Regularization type ('l1' or 'l2')
penalty = 'l1'  # You can change this to 'l1' if you want L1 regularization

# Train a logistic regression model for each column of y
L1_logistic_models = []
for i in range(matrix.shape[1]):
    # Create a logistic regression model with regularization
    clf = LogisticRegression(penalty=penalty, C=C, solver='liblinear')
    # Fit the model to the training data for the i-th column of y
    clf.fit(array, matrix[:, i])
    # Append the trained model to the list
    L1_logistic_models.append(clf)

# Predicting on the test set
y_pred = []
for clf in L1_logistic_models:
    y_pred.append(clf.predict(X_test))

# Convert the list of predictions into a 2D numpy array
y_pred = np.array(y_pred).T

# Calculate accuracy for each column and print
for i in range(y_test.shape[1]):
    accuracy = accuracy_score(y_test[:, i], y_pred[:, i])
    print(f"Accuracy for column {i+1}: {accuracy}")


print(np.sum(np.sum((y_pred == y_test), axis=0)/40000)/41, np.sum(np.sum((y_pred == y_test), axis=1)/41)/40000)

In [ ]:
from joblib import dump

# Save the model
dump(L2_logistic_models, 'L2_logistic_models.joblib')
dump(L1_logistic_models, 'L1_logistic_models.joblib')

## Processing test data

In [2]:
def parse_training_data(file_path):
    samples = []
    with open(file_path, 'r') as file:
        for line in file:
            sample = line.strip().split(' ')
            # m_labels = [int(label) for label in sample[0][2:].split(',')]
            # s_labels = [int(label) for label in sample[1][2:].split(',')]
            features = ' '.join(sample[2:])
            samples.append((features))
    return samples


test_data = parse_training_data("IE506_2024_progchallenge_test.txt")
test_data, len(test_data)

(['4949:0.19803 8044:0.22258 8144:0.15422 8586:0.17881 10181:0.14777 18149:0.08220 18398:0.11750 19982:0.11246 20575:0.23320 24137:0.15467 24478:0.09802 26804:0.05770 27306:0.10721 28752:0.06298 28940:0.21370 30752:0.36448 33010:0.12782 34478:0.14882 35015:0.22120 37663:0.13772 39723:0.10308 41295:0.23475 44956:0.24928 45500:0.08245 46693:0.26500',
  '23372:0.15737 31317:0.20145 33095:0.28638 33687:0.43445 33729:0.20024 34478:0.21648 35015:0.32176 37379:0.44524 40773:0.36230',
  '2138:0.05475 2301:0.07669 2642:0.17268 2643:0.15160 3079:0.09408 4664:0.16623 4671:0.03220 5641:0.13418 6410:0.16396 7876:0.09602 8008:0.11289 8032:0.10398 8071:0.05652 8608:0.05346 9191:0.04482 9574:0.13237 10255:0.07279 10263:0.08247 10382:0.20494 11100:0.07843 12122:0.03049 12152:0.08012 12982:0.10231 13606:0.06908 13819:0.06069 13820:0.08310 14636:0.07920 15285:0.07633 15669:0.06238 16503:0.07910 17776:0.10074 17982:0.17477 19200:0.08120 19294:0.11178 19507:0.06065 19544:0.12687 19584:0.09026 19762:0.07557

In [3]:
from scipy.sparse import dok_matrix
import numpy as np

array_shape = (150000, 47236)
# array = np.zeros(array_shape, dtype=np.float32)
test_array = dok_matrix(array_shape, dtype=np.float32)


# print(len(test_data))
# Iterate through each tuple
for i in range(len(test_data)):
    item = test_data[i]
    # print(item)
    tokens = item.split(" ")
    # print(len(tokens), tokens)
    # Iterate through each token
    for token in tokens:
        feature_id, value = token.split(':')

        feature_id = int(feature_id)
        value = float(value)
        # print(feature_id, value)

        test_array[i, feature_id] = value

test_array, test_array.shape 

(<150000x47236 sparse matrix of type '<class 'numpy.float32'>'
 	with 10969182 stored elements in Dictionary Of Keys format>,
 (150000, 47236))

## Prediction on test data

In [9]:
from joblib import load

L2_logistic_models_loaded = load("/home/23m1518/L2_logistic_models.joblib")
L1_logistic_models_loaded = load("/home/23m1518/L1_logistic_models.joblib")

y_pred_l2 = []
for clf in L2_logistic_models_loaded:
    y_pred_l2.append(clf.predict(test_array))

y_pred_l1 = []
for clf in L1_logistic_models_loaded:
    y_pred_l1.append(clf.predict(test_array))

In [4]:
y_pred_l2, y_pred_l1, len(y_pred_l2)

NameError: name 'y_pred_l2' is not defined

In [18]:
y_pred_l2 = np.array(y_pred_l2).T 
y_pred_l1 = np.array(y_pred_l1).T

y_pred_l2, y_pred_l2.shape, y_pred_l1, y_pred_l1.shape

(array([[1, 0, 0, ..., 0, 0, 0],
        [1, 0, 0, ..., 0, 0, 0],
        [1, 0, 1, ..., 0, 0, 0],
        ...,
        [1, 0, 0, ..., 0, 0, 0],
        [1, 0, 0, ..., 0, 0, 0],
        [0, 0, 1, ..., 0, 0, 0]]),
 (150000, 41),
 array([[1, 0, 0, ..., 0, 0, 0],
        [1, 0, 0, ..., 0, 0, 0],
        [1, 0, 1, ..., 0, 0, 0],
        ...,
        [1, 0, 0, ..., 0, 0, 0],
        [1, 0, 0, ..., 0, 0, 0],
        [0, 0, 1, ..., 0, 0, 0]]),
 (150000, 41))

## Making csv file for L2

In [3]:
import pandas as pd
from joblib import load

# labels_path = "category_labels.joblib"
category_labels = load("class_labels.joblib")
data_path = r"./"

# Define the filename to save
filename = "submission3.csv"
predictions = y_pred_l2

# Create the submission CSV file
with open(f"{data_path}/{filename}", 'w') as file:
    file.write("ID,M,S\n")
    for i in range(len(predictions)):
        M_list, S_list = [], []
        sample_pred = predictions[i, :]
        for j, (label, pred) in enumerate(zip(category_labels, sample_pred)):
            category, index = label.split("_")
            if category == 'M' and pred != 0:
                M_list.append(index)
            elif category == 'S' and pred != 0:
                S_list.append(index)

        if len(M_list) > 1 or len(S_list) > 1:
            M_list_str = f"\"{','.join(M_list)}\""
            S_list_str = f"\"{','.join(S_list)}\""
        else:
            M_list_str = ','.join(M_list)
            S_list_str = ','.join(S_list)

        entry = f"{i},{M_list_str},{S_list_str}\n"
        file.write(entry)

NameError: name 'y_pred_l2' is not defined

## Making csv file for L1

In [20]:
import pandas as pd
from joblib import load

# labels_path = "category_labels.joblib"
category_labels = load("class_labels.joblib")
data_path = r"./"

# Define the filename to save
filename = "submission3.csv"
predictions = y_pred_l2

# Create the submission CSV file
with open(f"{data_path}/{filename}", 'w') as file:
    file.write("ID,M,S\n")
    for i in range(len(predictions)):
        M_list, S_list = [], []
        sample_pred = predictions[i, :]
        for j, (label, pred) in enumerate(zip(category_labels, sample_pred)):
            category, index = label.split("_")
            if category == 'M' and pred != 0:
                M_list.append(index)
            elif category == 'S' and pred != 0:
                S_list.append(index)

        if len(M_list) > 1 or len(S_list) > 1:
            M_list_str = f"\"{','.join(M_list)}\""
            S_list_str = f"\"{','.join(S_list)}\""
        else:
            M_list_str = ','.join(M_list)
            S_list_str = ','.join(S_list)

        entry = f"{i},{M_list_str},{S_list_str}\n"
        file.write(entry)

0,['100'],['105']
1,['100'],['105']
2,"['100', '300']","['399']"
3,['400'],['496']
4,[],[]
5,['300'],['399']
6,['400'],['499']
7,['100'],[]
8,['300'],['399']
9,['100'],['123']
10,['300'],['399']
11,['300'],['361']
12,['100'],['105']
13,['300'],['399']
14,['100'],['105']
15,['400'],['495']
16,['300'],['399']
17,['100'],['105']
18,['100'],['105']
19,['400'],['494']
20,"['200', '300']","['236', '361']"
21,['400'],['496']
22,['300'],['399']
23,['400'],['496']
24,"['200', '300']","['361']"
25,['300'],['399']
26,['400'],['496']
27,['100'],[]
28,[],[]
29,['100'],[]
30,['300'],['399']
31,"['100']","['103', '115', '130']"
32,"['200', '400']","[]"
33,['100'],['105']
34,"['100']","['119', '122']"
35,['300'],['399']
36,['300'],['399']
37,[],[]
38,"['400']","['494', '496']"
39,['300'],['399']
40,['100'],['105']
41,['200'],['238']
42,['100'],['105']
43,['100'],['105']
44,"['100', '200', '300']","['399']"
45,"['100']","['105', '115']"
46,['100'],[]
47,['400'],['494']
48,['300'],['399']
49,['100'],['1

## ------------------------------------------------------------------------------------------------------------------------